In [1]:
import os
import utils
import configparser

In [2]:
# fix path variable
!docker --version
!python --version

Docker version 20.10.17, build 100c701
Python 3.8.2


### Load config from file

In [3]:
config = configparser.ConfigParser()
config.read('disaster_tweet_detect.config')
image_name = config['default']['image_name']
docker_repo = config['default']['docker_repo']
docker_usr = config['default']['docker_usr']
docker_pwd = config['default']['docker_pwd']
build_req = False
build_image = True
docker_upload = True
run_local = True
version = 1

### Build requirements.txt
**pipreqs** builds the requirements.txt based on the libraries used in the notebook. **nbconvert** is used to convert the notebook to a script that can be used by **pipreqs**. Additional line added to include **jupyter** as it is needed to run the Bokeh app.

In [4]:
if build_req:
    !pip freeze | grep -v disaster_tweet_detect > requirements.txt

### Build docker image
Image is build with the *image name*. The build will take a while on the first run because it needs to download the base image.

In [5]:
if build_image:
    # build docker image
    !(docker build -t {image_name} ..)

[+] Building 0.0s (0/1)                                                         
[+] Building 0.1s (2/3)                                                         
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 39B                                        0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 2B                                            0.0s
 => [internal] load metadata for docker.io/library/python:3.9              0.0s
[+] Building 0.3s (11/12)                                                       
 => [internal] load build definition from Dockerfile                       0.0s
 => => transferring dockerfile: 39B                                        0.0s
 => [internal] load .dockerignore                                          0.0s
 => => transferring context: 2B                                            0.0s
 => [internal] load metadata for dock

### Upload to private docker registry

Registry is hosted on a private NAS.

In [6]:
if docker_upload:
    !docker tag {image_name} {docker_repo}/{image_name}:{version}
    !docker login {docker_repo} -u {docker_usr} -p {docker_pwd}
    !docker push {docker_repo}/{image_name}:{version}

WARNING! Using --password via the CLI is insecure. Use --password-stdin.
Login Succeeded
The push refers to repository [dockerio.themaplevault.synology.me/disaster_tweet_detect]

a4868963: Preparing 
49c6ef30: Preparing 
ec62e589: Preparing 
542538b0: Preparing 
483a1684: Preparing 
2e051ea8: Waiting g 
bf18a086: Preparing 
7063fb95: Preparing 
177efc0c: Preparing 
b0d193bc: Waiting g 
5e673844: Preparing 
811d364e: Preparing 
260e173a: Preparing 
bb98b0dc: Preparing 
8387f467: Preparing 
c0c5405b: Layer already exists 1: digest: sha256:4d1bac7071df3cab273385fbc12705573e09f88aea7c12eb54569ab88b6e5b13 size: 3683


### Run docker image locally
Docker image will run on a docker server. The Streamlit server will run with its default port (80) but needs to be port forwarded by docker and is defined below.

In [7]:
if run_local:
    # define exposed port (docker port forwarding)
    port = 8501

    # run docker image
    command = utils.get_docker_run_command(port, image_name,
                                           debug=False)
    # command = utils.get_docker_run_command(port, image_name,
    #                                        local_dir_mount=os.getcwd(),
    #                                        debug=True)

    !{command}

2023-05-01 22:23:20.734 INFO    matplotlib.font_manager: generated new fontManager



  You can now view your Streamlit app in your browser.

  URL: http://0.0.0.0:80




KeyboardInterrupt

